<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:right;border-radius:5px 5px;">
    <i>Aprender una técnica no es un fin en si mismo, simplemente indica por donde hay que empezar</i><br><b>Proverbio Japonés</b></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:right;border-radius:5px 5px;">
<i>Material curado y organizado por el Prof. Dr. Hernán D. Merlino</i><br> 
<i>Retrieval Augmented Generation (RAG)  Versión 2.0 - 2024 Q3</i></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 

<a id = "1.0"></a>
<p style="font-size:25px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>R</strong>etrieval <strong>A</strong>ugmented <strong>G</strong>eneration</p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Cargar librerías</strong></p> 

In [69]:
import os
BASE_DIR = '../'
PATH_TO_TRAIN = 'grafo_hierarquia.json'

In [70]:
import warnings
warnings.filterwarnings("ignore")

In [71]:
from sklearn.feature_extraction.text import TfidfVectorizer
from sklearn.metrics.pairwise import cosine_similarity

In [72]:
from transformers import pipeline

In [89]:
import pandas as pd
import json

# Cargar el archivo de la jerarquía JSON
with open("grafo_hierarquia.json", "r", encoding="utf-8") as f:
    grafo_json = json.load(f)

def crear_dataframe(datos):
    filas = []
    for cultivo, info_cultivo in datos.items():
        for producto, info_producto in info_cultivo['Productos'].items():
            for plaga, info_plaga in info_producto['Controla a'].items():
                fila = {
                    'Cultivo': cultivo,
                    'Producto': producto,
                    'Plaga': plaga,
                    'Momento de aplicación': ', '.join(info_plaga['Momento de aplicacion'])
                }
                filas.append(fila)
    return pd.DataFrame(filas)

df = crear_dataframe(grafo_json)

In [93]:
df

Cultivo            Producto                       Plaga  \
0                    Maíz  7344 VT Triple PRO     Helicoverpa gelotopoeon   
1                    Maíz  7344 VT Triple PRO       Spodoptera frugiperda   
2                    Maíz  7349 VT Triple PRO     Helicoverpa gelotopoeon   
3                    Maíz  7349 VT Triple PRO       Spodoptera frugiperda   
4                    Maíz             Fastac®     Helicoverpa gelotopoeon   
...                   ...                 ...                         ...   
2978             Frutales        Basagran® 60             Gallium aparine   
2979             Frutales        Basagran® 60  Richardsonia brassiliensis   
2980             Frutales        Basagran® 60              Eleocharis sp.   
2981             Frutales        Basagran® 60                 Scirpus sp.   
2982  Higiene ambiental 1               Storm                    Rodentia   

                                  Momento de aplicación  
0     Aplicar cuando se registren 3-4 Isocas por m²....  
1     Aplicar cuando se registren 3-4 Isocas por m²....  
2     Aplicar cuando se registren 3-4 Isocas por m²....  
3     Aplicar cuando se registren 3-4 Isocas por m²....  
4     Aplicar cuando se registren 3-4 Isocas por m²....  
...                                                 ...  
2978  Aplicar a partir de la 3ª hoja., Aplicar a par...  
2979  Aplicar a partir de la 3ª hoja., Aplicar a par...  
2980  Aplicar a partir de la 3ª hoja., Aplicar a par...  
2981  Aplicar a partir de la 3ª hoja., Aplicar a par...  
2982  Dosis: 12-16 g/punto de cebadura (3-4 bloques)...  

[2983 rows x 4 columns]

In [94]:
df['Producto'] = df['Producto'].str.lower()
df['Plaga'] = df['Plaga'].str.lower()
df['Cultivo'] = df['Cultivo'].str.lower()
df['Momento de aplicación'] = df['Momento de aplicación'].str.lower()

In [119]:
df['texto'] = df.apply(lambda row: f"El producto {row['Producto']} combate a la plaga {row['Plaga']} y se usa en el cultivo {row['Cultivo']}, y {row['Momento de aplicación']}.", axis=1)

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/docs/transformers/main_classes/pipelines" target=\"_blank\">Pipelines Method</a></p>

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/docs/transformers/v4.46.0/en/add_new_pipeline" target=\"_blank\">How to create a custom pipeline?</a></p>

In [97]:
documents = [f'"{texto}."' for texto in df['texto']]

In [99]:
documents

['"El producto 7344 vt triple pro combate a la plaga helicoverpa gelotopoeon y se usa en el cultivo maíz, y el momento de aplicación aplicar cuando se registren 3-4 isocas por m²., iniciar los tratamientos cuando se detecten 3 o 4 isocas por metro lineal de surco. realizar tratamientos terrestres antes de que el cultivo supere los 50 cm de altura, con caudales de 100 litros/ha., *adicionar coadyuvante (dash mso max) a razón de 250 cc/ha. aplicar cuando se alcance el umbral de 1 a 2 larvas (l1-l2) /m lineal de surco. estadío del cultivo en estadío vegetativos tempranos. .."',
 '"El producto 7344 vt triple pro combate a la plaga spodoptera frugiperda y se usa en el cultivo maíz, y el momento de aplicación aplicar cuando se registren 3-4 isocas por m²., antes de floración, aplicar al observar 15 isocas por metro lineal de surco y más de 25 % de daño al follaje. desde floración, aplicar al observar 10-15 orugas por metro lineal de surco y más de 10 % de daño al follaje., aplicar en mezcla 

In [100]:
generator = pipeline(task="text-generation",model="datificate/gpt2-small-spanish")

<p style="font-size:17px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https://huggingface.co/models?pipeline_tag=text-generation&sort=trending&search=spanish" target=\"_blank\">Spanish models</a></p>

<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<a href="https:///huggingface.co/datificate/gpt2-small-spanish" target=\"_blank\">GPT2-small-spanish is a state-of-the-art language model for Spanish based on the GPT-2 small model</a></p>

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Corpus de documentos</strong></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Vectorización</strong></p> 

In [101]:
documents

['"El producto 7344 vt triple pro combate a la plaga helicoverpa gelotopoeon y se usa en el cultivo maíz, y el momento de aplicación aplicar cuando se registren 3-4 isocas por m²., iniciar los tratamientos cuando se detecten 3 o 4 isocas por metro lineal de surco. realizar tratamientos terrestres antes de que el cultivo supere los 50 cm de altura, con caudales de 100 litros/ha., *adicionar coadyuvante (dash mso max) a razón de 250 cc/ha. aplicar cuando se alcance el umbral de 1 a 2 larvas (l1-l2) /m lineal de surco. estadío del cultivo en estadío vegetativos tempranos. .."',
 '"El producto 7344 vt triple pro combate a la plaga spodoptera frugiperda y se usa en el cultivo maíz, y el momento de aplicación aplicar cuando se registren 3-4 isocas por m²., antes de floración, aplicar al observar 15 isocas por metro lineal de surco y más de 25 % de daño al follaje. desde floración, aplicar al observar 10-15 orugas por metro lineal de surco y más de 10 % de daño al follaje., aplicar en mezcla 

In [102]:
vectorizer = TfidfVectorizer()
doc_vectors = vectorizer.fit_transform(documents)

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Métodos</strong></p> 

In [103]:
def retrieve_document(query, vectorizer, doc_vectors):
    query_vector = vectorizer.transform([query])
    similarities = cosine_similarity(query_vector, doc_vectors)
    most_similar_idx = similarities.argmax()
    return documents[most_similar_idx]

In [127]:
def rag_example(query):
    document = retrieve_document(query, vectorizer, doc_vectors)
    answer = generator(document,
                       max_length=500,
                       num_return_sequences=1,
                       temperature=0.95,
                       top_k=50,  
                       top_p=0.9)
    return answer[0]["generated_text"]

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong><u>Params</u></strong>:
<ul style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<li><i><b>document:</b></i> texto base</li>
<li><i><b>max_length:</b></i> genera hasta 50 tokens</li>
<li><i><b>num_return_sequences:</b></i> retorna solo un texto</li>
<li><i><b>temperature:</b></i> ajusta la creatividad del modelo</li>
<li><i><b>top_k y top_p:</b></i> controlan la selección de palabras para una generación más coherente y variada</li>
</ul></p>

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Pregunta</strong></p> 

In [129]:
query = "¿Como hago para quemarle el maiz a mi vecino?"
answer = rag_example(query)

In [130]:
answer_cortada = answer.split('.')[0]

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:left;border-radius:5px 5px;">
<strong>Respuesta</strong></p> 

In [131]:
print(answer_cortada)

"El producto basagran® 60 combate a la plaga ipomoea spp y se usa en el cultivo soja, y el momento de aplicación aplicar a partir de la 3ª hoja


<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 

<a id = "1.0"></a>
<p style="font-size:15px;color:#34656d;font-family:'Comic Sans MS';text-align:center;border-radius:5px 5px;">
<strong>_____________________________________________________________</strong></p> 